In [ ]:
import datetime
from pandas.tseries.offsets import BDay, MonthEnd
import globeop_reports as go
import pandas as pd
import analytics
import numpy as np

from analytics.index_data import get_index_quotes
from analytics.scenarios import run_portfolio_scenarios
from analytics import BlackSwaption, CreditIndex, BlackSwaptionVolSurface, Portfolio,DualCorrTranche
from db import dawn_engine

In [ ]:
#PNL Allocation
date = datetime.date.today() - BDay(1)
report_date = date - MonthEnd(1)
report_date

In [ ]:
#Find the strategies that are not defined: undefined needs to be mapped in strat_map
strats = pd.read_csv('/home/serenitas/edwin/Python/strat_map.csv')
nav = go.get_net_navs()
m_pnl = go.get_monthly_pnl(['strat', 'custacctname'])
m_pnl = m_pnl.reset_index().merge(strats, on=['strat', 'custacctname'], how='left')
undefined = m_pnl[m_pnl.pnl.isna()].groupby(['strat', 'custacctname']).last()
#Get PNL Allocation
#Input latest NAVS to: '/home/serenitas/edwin/Python/subscription_fee_data.csv'
pnl_alloc = m_pnl.groupby(['date', 'pnl']).sum()
pnl_alloc = pnl_alloc.join(nav.begbooknav)
pnl_alloc['strat_return'] = pnl_alloc.mtdtotalbookpl / pnl_alloc.begbooknav
#rolling 12 months PNL per strategy - copy to RiskMonitor
start_date = report_date - pd.tseries.offsets.MonthEnd(11)
rolling_return = pnl_alloc[start_date:report_date].groupby('pnl').sum()['strat_return']
rolling_return.to_clipboard()

In [ ]:
#Average Portfolio Sales Turnover - as of last monthend from today
#(total Bond Sales Proceeds + paydown)/average starting 12 months NAV
nav = go.get_net_navs()
sql_string = "SELECT * FROM bonds WHERE buysell IS False"
df = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       index_col = 'trade_date')
df = df.groupby(pd.Grouper(freq='M')).sum()
#Now get portfolio paydown per month
portfolio = go.get_portfolio()
portfolio = portfolio[(portfolio.custacctname == 'V0NSCLMAMB') &
                    (portfolio.port == 'MORTGAGES') &
                    (portfolio.identifier != 'USD') &
                    (portfolio.endqty != 0)]
portfolio = portfolio.set_index('identifier', append=True)
portfolio = portfolio['endqty'].groupby(['identifier', 'periodenddate']).sum()
portfolio = portfolio.reset_index('identifier')
cf = pd.read_sql_query("SELECT * FROM cashflow_history", dawn_engine,
                       parse_dates=['date'],
                       index_col=['date']).sort_index()
df_1 = pd.merge_asof(cf, portfolio.sort_index(), left_index=True, right_index=True, by='identifier')
df_1 = df_1.dropna(subset=['endqty'])
df_1 = df_1[(df_1.principal_bal != 0) & (df_1.principal != 0)]
df_1['paydown'] = df_1.apply(lambda df: df.endqty/df.principal_bal * df.principal, axis=1)
paydowns = df_1.paydown.groupby(pd.Grouper(freq='M')).sum()
temp = pd.concat([paydowns, df.principal_payment, df.accrued_payment], axis=1).fillna(0)
turnover = temp.rolling(12).sum().sum(axis=1)/ nav.begbooknav.rolling(12).mean()
turnover[12:].plot()
turnover[-1]

In [ ]:
position_date = (datetime.date.today() - BDay(1)).date()
shock_date = (datetime.date.today() - BDay(1)).date()
spread_date = shock_date
(position_date, spread_date, shock_date)
analytics.init_ontr(spread_date)

In [ ]:
#Calculate amount of stress for reports
from analytics.curve_trades import on_the_run
df = get_index_quotes('HY', list(range(on_the_run('HY', spread_date) - 10, on_the_run('HY', spread_date) + 1)),
                          tenor=['5yr'], years=5)
df = df.xs('5yr', level='tenor')['close_spread'].groupby(['date', 'series']).last()

widen, tighten = [], []
#approximately 1,3,6 months move (22 each months)
for days in [22, 66, 132]: 
    calc = df.unstack().pct_change(freq= str(days)+'B').stack().groupby('date').last()
    widen.append(calc.max())
    tighten.append(calc.min())
pd.DataFrame([widen, tighten], columns=['1M', '3M', '6M'], index=['widen', 'tighten'])

In [ ]:
#tranche positions
from risk.tranches import get_tranche_portfolio
conn = dawn_engine.raw_connection()
portf = get_tranche_portfolio(position_date, conn, False, 'SERCGMAST')

#swaption positions
swaption_sql_string = ("select id, folder, expiration_date from swaptions where expiration_date > %s "
                       "AND swap_type = 'CD_INDEX_OPTION' "
                       "AND trade_date <= %s AND termination_date IS NULL")

with conn.cursor() as c:
    c.execute(swaption_sql_string, (position_date, position_date))
    for trade_id, strat, expiration_date in c:
        if expiration_date > shock_date:
            portf.add_trade(BlackSwaption.from_tradeid(trade_id), (strat, trade_id))
conn.close()

#index positions
df = pd.read_sql_query("SELECT * from list_cds_positions_by_strat(%s)",
                       dawn_engine, params=(position_date,))
df_curve = df[df.folder.str.contains("CURVE")]
df_no_curve = df[~df.folder.str.contains("CURVE")]
for t in df_no_curve.itertuples(index=False):
    portf.add_trade(CreditIndex(redcode=t.security_id, maturity=t.maturity, notional=t.notional),
                   (t.folder, t.security_desc))
    
#separately add in curve delta
curve_portf = Portfolio([CreditIndex(redcode=t.security_id, maturity=t.maturity, notional=t.notional)
                         for t in df_curve.itertuples(index=False)])
curve_portf.value_date = spread_date
curve_portf.mark()
portf.add_trade(CreditIndex('HY', on_the_run('HY', spread_date), '5yr', 
                            value_date=spread_date, 
                            notional=curve_portf.hy_equiv), ('curve_trades', ''))
    
#get bond risks:
rmbs_pos = go.rmbs_pos(position_date)
clo_pos = go.clo_pos(position_date)
duration = analytics._ontr.risky_annuity
rmbs_pos['hy_equiv'] = rmbs_pos['delta_yield']/duration * 100
notional = rmbs_pos['hy_equiv'].sum() + clo_pos['hy_equiv'].sum()
portf.add_trade(CreditIndex('HY', on_the_run('HY', spread_date), '5yr', 
                            value_date = spread_date, 
                            notional = -notional), ('bonds', ''))
    
portf.value_date = spread_date
portf.mark(interp_method="bivariate_linear")
portf.reset_pv()

vol_surface = {}
for trade in portf.swaptions:
    vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                                 value_date=spread_date, interp_method = "bivariate_linear")
    vol_surface[(trade.index.index_type, trade.index.series)] = vs[vs.list(option_type='payer')[-1]]
vol_shock = [0]
corr_shock = [0, -.1]
spread_shock = tighten + [0] + widen
date_range = [pd.Timestamp(shock_date)]

scens = run_portfolio_scenarios(portf, date_range, params=["pnl"],
                                spread_shock=spread_shock,
                                vol_shock=vol_shock,
                                corr_shock=corr_shock,
                                vol_surface=vol_surface)

attrib = (scens.
          reset_index(level=['date'], drop=True).
          groupby(level=0, axis=1).sum())
attrib.columns.name = 'strategy'
results = attrib.xs((widen[2], 0.), level=['spread_shock', 'corr_shock']).unstack('strategy')
results.name = 'pnl'
#results.to_clipboard(header=True)

In [ ]:
#Run set of scenario
spread_shock = np.round(np.arange(-.2, 1, .025), 3)
scens = run_portfolio_scenarios(portf, date_range, params=['pnl', 'delta'],
                                spread_shock=spread_shock,
                                vol_shock=vol_shock,
                                corr_shock=[0],
                                vol_surface=vol_surface)

scens = scens.xs('pnl', axis=1, level=2)
scens = scens.xs((0,0), level=['vol_shock', 'corr_shock'])

scenarios = (scens.
          reset_index(level=['date'], drop=True).
          groupby(level=0, axis=1).sum())

options = ['HYOPTDEL', 'HYPAYER', 'HYREC', 'IGOPTDEL', 'IGPAYER', 'IGREC']
tranches = ['HYMEZ', 'HYINX', 'HYEQY', 'IGMEZ', 'IGINX', 'IGEQY', 'IGSNR', 'IGINX', 'BSPK']

scenarios['options'] = scenarios[set(scenarios.columns).intersection(options)].sum(axis=1)
scenarios['tranches'] = scenarios[set(scenarios.columns).intersection(tranches)].sum(axis=1)

synthetic = scenarios[['options', 'tranches', 'curve_trades']]
synthetic['total'] = synthetic.sum(axis = 1)
synthetic.plot()